In [201]:
import os

import joblib
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pyspark.sql import SparkSession
from pyspark.sql.functions import col
from statsforecast import StatsForecast
from statsforecast.models import AutoARIMA
from statsmodels.tsa.seasonal import seasonal_decompose
from prophet import Prophet

In [202]:
df = pd.read_csv('./output/sor/ipeadata.csv')

In [203]:
df = df.drop(columns=["sercodigo", "tercodigo", "nivnome"])
df = df.rename(columns={"valdata": "data", "valvalor": "preco"})
df = df.dropna(subset=["preco", "data"])
df = df.sort_values(by="data", ascending=False)
df['data'] = pd.to_datetime(df['data'], utc=True).dt.tz_localize(None).dt.normalize()

df_ipea = df.copy()
df_ipea['data'] = pd.to_datetime(df_ipea['data']).dt.tz_localize(None).dt.normalize()
df_ipea = df_ipea.sort_values('data', ascending=False).set_index('data')

print(df_ipea)

            preco
data             
2024-11-04  74.89
2024-11-01  73.63
2024-10-31  73.25
2024-10-30  73.21
2024-10-29  71.09
...           ...
1987-05-26  18.63
1987-05-25  18.60
1987-05-22  18.55
1987-05-21  18.45
1987-05-20  18.63

[11292 rows x 1 columns]


In [204]:
plotly_conf = {'template': 'ggplot2', 'color_sequence': ['#3d183d']}

In [205]:
df_ipea.describe()

preco
count  11292.000000
mean      53.311948
std       33.164669
min        9.100000
25%       20.610000
50%       48.885000
75%       76.810000
max      143.950000

Distribuição das variáveis

In [206]:
# Alterando a cor do gráfico para um tom mais claro

fig = px.histogram(
    data_frame=df_ipea,
    x='preco',
    nbins=20,
    template=plotly_conf['template'],
    color_discrete_sequence=plotly_conf['color_sequence']
)

# Atualizando o layout com ajustes nos títulos e margens
fig.update_layout(
    title='Distribuição dos Preços do Petróleo Brent',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Preço (US$)',
    yaxis_title='Frequência',
    xaxis=dict(tickangle=0, title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    width=1600,
    height=600,
    margin=dict(l=80, r=40, t=80, b=80)
)

# Exibir o gráfico
fig.show()

In [207]:
df_ipea_log = df_ipea[df_ipea['preco'] > 0]  # Remove valores não positivos
df_ipea_log['log_preco'] = np.log(df_ipea_log['preco'])  # Aplica o logaritmo natural

# Criação do histograma
fig = px.histogram(
    data_frame=df_ipea_log,
    x='log_preco',  
    nbins=20,
    template=plotly_conf['template'],
    color_discrete_sequence=plotly_conf['color_sequence']
)

# Atualização do layout do gráfico
fig.update_layout(
    title='Histograma do Log do Preço do Petróleo Brent',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Log do Preço (US$)',
    yaxis_title='Frequência',
    xaxis=dict(tickangle=0, title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    width=1600,
    height=600,
    margin=dict(l=80, r=40, t=80, b=80)
)
# Exibir o gráfico
fig.show()

In [208]:
# Criação do boxplot
fig = px.box(
    data_frame=df_ipea,
    x='preco',
    template=plotly_conf['template'],
    color_discrete_sequence=plotly_conf['color_sequence']
)

# Atualização do layout
fig.update_layout(
    title='Boxplot do Preço do Petróleo Brent',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Preço (US$)',
    xaxis=dict(tickangle=0, title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis_title='Volume',
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    width=1600,
    height=600,
    margin=dict(l=80, r=40, t=80, b=80)
)

# Exibir o gráfico
fig.show()

Analisando a série

In [209]:
resultados = seasonal_decompose(df_ipea, period=5)

In [210]:
tendencia_df = resultados.trend.to_frame(name="Tendência")  # Tendência (Média Móvel)
sazonalidade_df = resultados.seasonal.to_frame(name="Sazonalidade")  # Componente sazonal
residuos_df = resultados.resid.to_frame(name="Resíduos")  # Componente residual

fig = make_subplots(
    rows=4, cols=1,
    subplot_titles=(
        "Série Original", 
        "Tendência (Média Móvel)", 
        "Sazonalidade", 
        "Resíduos"
    )
)

fig.add_trace(
    go.Scatter(
        x=df_ipea.index, 
        y=df_ipea['preco'], 
        name='Série Original', 
        marker=dict(color='#00008B')  # Azul escuro
    ), 
    row=1, col=1
)

fig.add_trace(
    go.Scatter(
        x=tendencia_df.index, 
        y=tendencia_df["Tendência"], 
        name='Tendência (Média Móvel)', 
        marker=dict(color='#B22222')  # Vermelho tijolo
    ), 
    row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=sazonalidade_df.index, 
        y=sazonalidade_df["Sazonalidade"], 
        name='Sazonalidade', 
        marker=dict(color='#008000')  # Verde
    ), 
    row=3, col=1
)

fig.add_trace(
    go.Scatter(
        x=residuos_df.index, 
        y=residuos_df["Resíduos"], 
        name='Resíduos', 
        marker=dict(color='gold')  # Dourado
    ), 
    row=4, col=1
)

fig.update_layout(
    title={
        'text': 'Decomposição da Série de Preços do Petróleo Brent',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 24}
    },
    width=1600,
    height=1200,
    margin=dict(l=80, r=40, t=80, b=80),
    template=plotly_conf['template']
)

fig.show()


Analisando sazonalidade

In [211]:
# Filtrando os dados a partir de 1º de janeiro de 2023
df_ipea_filtrado = df_ipea.loc[df_ipea.index >= '2023-01-01']

# Decomposição sazonal com período definido
resultados_sazonalidade = seasonal_decompose(df_ipea_filtrado, period=5)
sazonalidade_df = resultados_sazonalidade.seasonal.to_frame(name="Sazonalidade")

# Criando o gráfico de linha para a sazonalidade
fig = px.line(
    sazonalidade_df,
    y="Sazonalidade",
    template=plotly_conf['template'],
    color_discrete_sequence=plotly_conf['color_sequence']
)

# Atualizando o layout do gráfico
fig.update_layout(
    title='Sazonalidade da Série de Preços do Petróleo Brent',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Período',
    xaxis=dict(tickangle=0, title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis_title='Sazonalidade',
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    showlegend=False,
    width=1600,
    height=600,
    margin=dict(l=100, r=20, t=80, b=80)
)

# Exibindo o gráfico
fig.show()

Preparação dos dados

In [212]:
# Preparando o DataFrame para modelagem
df_dados = df[['data', 'preco']].rename(columns={'data': 'ds', 'preco': 'y'})
df_dados['unique_id'] = 'Preco' 
df_dados = df_dados.dropna().sort_values('ds', ascending=False) 

# Exibindo as primeiras linhas do DataFrame preparado
df_dados.head()

ds      y unique_id
13561 2024-11-04  74.89     Preco
13560 2024-11-01  73.63     Preco
13559 2024-10-31  73.25     Preco
13558 2024-10-30  73.21     Preco
13557 2024-10-29  71.09     Preco

In [213]:
data_max = df_dados.ds.max()
dias_anteriores = 30
data_min = pd.to_datetime('2000-01-01')
data_max_anterior_dias = data_max - pd.Timedelta(days=dias_anteriores)
data_max_anterior_meses = (data_max.replace(day=1) - pd.DateOffset(months=6)).replace(day=1)

In [214]:
print("Data Max:", data_max)
print("Data Min:", data_min)
print("Data dias anteriores:", data_max_anterior_dias)
print("Primeira Data do Mes, por meses anteriores:", data_max_anterior_meses)

Data Max: 2024-11-04 00:00:00
Data Min: 2000-01-01 00:00:00
Data dias anteriores: 2024-10-05 00:00:00
Primeira Data do Mes, por meses anteriores: 2024-05-01 00:00:00


In [215]:
# Dividindo os dados em conjuntos de treino e teste
treino_a = df_dados[(df_dados['ds'] >= data_min) & (df_dados['ds'] < data_max_anterior_dias)]
teste_a = df_dados[df_dados['ds'] >= data_max_anterior_dias]

# Calculando o horizonte de previsão
h = teste_a['ds'].nunique()

In [216]:
treino_p = treino_a.reset_index(drop=True).drop('unique_id', axis=1)
teste_p = teste_a.drop('unique_id', axis=1).set_index('ds', drop=True)

In [217]:
# Configurando e ajustando o modelo ARIMA
modelo_arima = StatsForecast(
    models=[AutoARIMA(season_length=5)],  # Configurações do modelo
    freq='B',  # Frequência de dias úteis
    n_jobs=-1  # Uso de múltiplos núcleos para paralelismo
)

# Ajustando o modelo aos dados de treino
modelo_arima.fit(treino_a)

# Realizando a previsão para o horizonte definido
forecast_arima = modelo_arima.predict(h=h, level=[90])

# Adicionando as datas ao DataFrame de previsão
forecast_arima['ds'] = teste_a['ds'].to_list()

# Unindo as previsões com os dados reais para análise
forecast_arima = (
    forecast_arima
    .reset_index()  # Redefine o índice
    .merge(teste_a, on=['ds', 'unique_id'], how='left')  # Faz o merge com os dados de teste
)

# Exibindo o DataFrame final com previsões e valores reais
forecast_arima

/home/spark/source/repos/fiap-dataanalysis-techchallenge-fase4/.venv/lib/python3.12/site-packages/statsforecast/core.py:494: FutureWarning:

In a future version the predictions will have the id as a column. You can set the `NIXTLA_ID_AS_COL` environment variable to adopt the new behavior and to suppress this warning.



unique_id         ds  AutoARIMA  AutoARIMA-lo-90  AutoARIMA-hi-90      y
0      Preco 2024-11-04  78.739015        76.063147        81.414883  74.89
1      Preco 2024-11-01  78.263017        74.784419        81.741615  73.63
2      Preco 2024-10-31  78.685417        74.785180        82.585654  73.25
3      Preco 2024-10-30  79.049724        74.763346        83.336102  73.21
4      Preco 2024-10-29  79.015259        74.209702        83.820816  71.09
5      Preco 2024-10-28  78.971857        73.718991        84.224724  71.87
6      Preco 2024-10-25  78.980158        73.332943        84.627373  75.62
7      Preco 2024-10-24  79.044513        73.013626        85.075401  74.27
8      Preco 2024-10-23  78.967135        72.555013        85.379256  74.68
9      Preco 2024-10-22  78.943209        72.171804        85.714615  75.59
10     Preco 2024-10-21  79.004248        71.912683        86.095813  73.29
11     Preco 2024-10-18  79.049326        71.640086        86.458567  72.75
12     Preco 2024-10-17  79.059381        71.335748        86.783015  74.37
13     Preco 2024-10-16  79.079894        71.051014        87.108774  73.65
14     Preco 2024-10-15  79.109773        70.785944        87.433603  73.68
15     Preco 2024-10-12  79.132141        70.518331        87.745951  78.47
16     Preco 2024-10-11  79.149814        70.251770        88.047858  80.27
17     Preco 2024-10-10  79.169425        69.993381        88.345470  79.45
18     Preco 2024-10-09  79.188712        69.740338        88.637087  77.06
19     Preco 2024-10-08  79.205627        69.489735        88.921519  78.19
20     Preco 2024-10-07  79.221434        69.242860        89.200008  81.74

In [218]:
# Gerando os limites da banda de confiança
banda_sup_arima = forecast_arima['AutoARIMA-hi-90'].to_list()  # Limite superior
banda_inf_arima = forecast_arima['AutoARIMA-lo-90'].to_list()  # Limite inferior invertido
banda_arima = banda_sup_arima + banda_inf_arima[::-1]  # Concatenando superior com inferior invertido

# Gerando o índice contínuo para a banda
banda_arima_index = forecast_arima['ds'].to_list()  # Datas originais
banda_arima_index += banda_arima_index[::-1]  # Concatenando com as datas em ordem inversa

# Filtrando e ajustando o conjunto de treino
treino_filtrado = treino_a.drop(columns='unique_id').set_index('ds')
treino_filtrado = treino_filtrado[(treino_filtrado.index >= data_max_anterior_meses) & (treino_filtrado.index < data_max_anterior_dias)]

# Ajustando o conjunto de teste
teste_filtrado = teste_a.drop(columns='unique_id').set_index('ds')

# Concatenando os dados de treino e teste
base_arima = pd.concat([teste_filtrado, treino_filtrado]).rename(columns={'y': 'Preço'})

# Exibindo as primeiras linhas do DataFrame resultante
base_arima.head()

Preço
ds               
2024-11-04  74.89
2024-11-01  73.63
2024-10-31  73.25
2024-10-30  73.21
2024-10-29  71.09

In [219]:
# Criando o gráfico principal da série temporal
fig = px.line(
    base_arima,
    template=plotly_conf['template'],
    color_discrete_sequence=['#00008B']  # Azul escuro para a série base
)

# Adicionando a banda de confiança
fig.add_scatter(
    x=banda_arima_index, 
    y=banda_arima,
    name='Banda de Confiança',
    mode='lines',
    line=dict(color='#B22222', width=0),  # Vermelho tijolo com largura zero
    fill='toself',  # Preenchimento para criar a banda
    opacity=0.5     # Transparência para visualização clara
)

# Adicionando a linha de previsão
fig.add_scatter(
    x=forecast_arima['ds'], 
    y=forecast_arima['AutoARIMA'], 
    name='Preço Previsto',
    mode='lines+markers',
    line=dict(color='#B22222'),  # Vermelho tijolo para previsões
    marker=dict(size=6)
)

# Atualizando o layout do gráfico
fig.update_layout(
    title='Previsão de Preços do Petróleo Brent com ARIMA',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Período',
    xaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis_title='Preço do Petróleo Brent (US$)',
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    legend_title='Legenda',
    legend=dict(font=dict(size=12)),
    width=1600,
    height=600,
    margin=dict(l=100, r=20, t=80, b=80)
)

# Exibindo o gráfico
fig.show()


Prophet

In [220]:
modelo_prophet = Prophet()
modelo_prophet.fit(treino_p)

12:01:21 - cmdstanpy - INFO - Chain [1] start processing
12:01:31 - cmdstanpy - INFO - Chain [1] done processing


In [221]:
# Generate a future DataFrame with 90 days
future = modelo_prophet.make_future_dataframe(periods=dias_anteriores, freq='D', include_history=False)

# Exclude weekends from the future DataFrame
future = future[future['ds'].dt.weekday < h].reset_index(drop=True)

# Display the future DataFrame
future

ds
0  2024-10-05
1  2024-10-06
2  2024-10-07
3  2024-10-08
4  2024-10-09
5  2024-10-10
6  2024-10-11
7  2024-10-12
8  2024-10-13
9  2024-10-14
10 2024-10-15
11 2024-10-16
12 2024-10-17
13 2024-10-18
14 2024-10-19
15 2024-10-20
16 2024-10-21
17 2024-10-22
18 2024-10-23
19 2024-10-24
20 2024-10-25
21 2024-10-26
22 2024-10-27
23 2024-10-28
24 2024-10-29
25 2024-10-30
26 2024-10-31
27 2024-11-01
28 2024-11-02
29 2024-11-03

In [222]:
# Realizando a previsão com o modelo Prophet
forecast_prophet = modelo_prophet.predict(future)

# Selecionando colunas relevantes: datas, previsões e intervalos de confiança
forecast_prophet = forecast_prophet[['ds', 'yhat', 'yhat_lower', 'yhat_upper']]

# Exibindo o DataFrame com previsões
forecast_prophet.head()


ds       yhat  yhat_lower  yhat_upper
0 2024-10-05  89.891442   76.033087  103.198289
1 2024-10-06  89.484266   75.996057  103.332659
2 2024-10-07  89.539764   76.548586  102.327085
3 2024-10-08  89.531908   76.322700  103.029447
4 2024-10-09  89.489912   76.077245  102.167668

In [223]:
# Gerando os limites da banda de confiança
banda_sup = forecast_prophet['yhat_upper'].to_list()  # Limite superior
banda_inf = forecast_prophet['yhat_lower'].to_list()  # Limite inferior invertido
banda_conf = banda_sup + banda_inf[::-1]  # Concatenando limite superior com inferior invertido

# Gerando o índice contínuo para a banda
banda_index = forecast_prophet['ds'].to_list()  # Datas originais
banda_index += banda_index[::-1]  # Concatenando datas em ordem inversa

# Ajustando o conjunto de treino
treino_filtrado = treino_p.set_index('ds')
treino_filtrado = treino_filtrado[(treino_filtrado.index >= data_max_anterior_meses) & (treino_filtrado.index < data_max)]

# Mantendo o conjunto de teste como está
teste_filtrado = teste_p

# Concatenando treino e teste
base_prophet = pd.concat([teste_filtrado, treino_filtrado]).rename(columns={'y': 'Preço'})

# Unindo as previsões com os dados reais
forecast_prophet = pd.merge(forecast_prophet, teste_p, on='ds')

# Configurando a coluna 'ds' como índice
forecast_prophet.set_index('ds', inplace=True)

# Exibindo o DataFrame resultante
forecast_prophet.head()


yhat  yhat_lower  yhat_upper      y
ds                                                  
2024-10-07  89.539764   76.548586  102.327085  81.74
2024-10-08  89.531908   76.322700  103.029447  78.19
2024-10-09  89.489912   76.077245  102.167668  77.06
2024-10-10  89.625992   76.748759  102.224978  79.45
2024-10-11  89.684655   76.676263  103.641832  80.27

In [224]:
# Gráfico principal da série temporal
fig = px.line(
    base_prophet,
    template=plotly_conf['template'],
    color_discrete_sequence=['#00008B']  # Azul escuro para a série base
)

# Adicionando a banda de confiança
fig.add_scatter(
    x=banda_index, 
    y=banda_conf,
    name='Banda de Confiança',
    mode='lines',
    line=dict(color='#B22222', width=0),  # Vermelho tijolo com largura zero
    fill='toself',  # Preenchimento para criar a banda
    opacity=0.5     # Transparência para visualização clara
)

# Adicionando a linha de previsão
fig.add_scatter(
    x=forecast_prophet.index, 
    y=forecast_prophet['yhat'], 
    name='Preço Previsto',
    mode='lines+markers',
    line=dict(color='#B22222'),  # Vermelho tijolo para previsões
    marker=dict(size=6)  # Tamanho dos marcadores
)

# Atualizando o layout do gráfico
fig.update_layout(
    title='Previsão de Preços do Petróleo Brent com Prophet',
    title_font=dict(size=20, family='Arial', color='black'),
    xaxis_title='Período',
    xaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    yaxis_title='Preço do Petróleo Brent (US$)',
    yaxis=dict(title_font=dict(size=14), tickfont=dict(size=12)),
    legend_title='Legenda',
    legend=dict(font=dict(size=12)),
    width=1600,
    height=600,
    margin=dict(l=100, r=20, t=80, b=100)
)

# Exibindo o gráfico
fig.show()


In [225]:
#função para validação dos modelos
def wmape(y_true, y_pred):
    return np.abs(y_true - y_pred).sum() / np.abs(y_true).sum()

In [226]:
wmape_arima = wmape(forecast_arima['y'].values, forecast_arima['AutoARIMA'].values)
wmape_prophet = wmape(forecast_prophet['y'].values, forecast_prophet['yhat'].values)
print(f'ARIMA - WAPE : {wmape_arima:.2%} | Acurácia : {1 - wmape_arima:.2%}')
print(f'PROPHET - WAPE : {wmape_prophet:.2%} | Acurácia : {1 - wmape_prophet:.2%}')

ARIMA - WAPE : 5.43% | Acurácia : 94.57%
PROPHET - WAPE : 18.51% | Acurácia : 81.49%


Acurácia de 94.57% significa que o modelo prevê corretamente, em média, 94.57% dos valores reais.
O restante 5.43% representa o erro médio proporcional aos valores reais.


Exportando modelo

In [227]:
# Preparando os dados
df_preparado = df[['data', 'preco']].rename(columns={'data': 'ds', 'preco': 'y'})
df_preparado['unique_id'] = 'Preco'
df_preparado.dropna(inplace=True)

# Definindo os dados de treino e o horizonte de previsão
treino = df_preparado.loc[df_preparado['ds'] >= '2000-01-01']  # Filtrando dados desde 2000
h = 30 # Previsão para 30 dias

# Treinando o modelo AutoARIMA
modelo_arima = StatsForecast(models=[AutoARIMA(season_length=5)], freq='B', n_jobs=-1)
modelo_arima.fit(treino)

StatsForecast(models=[AutoARIMA])

In [228]:
# Salvando o modelo treinado
joblib.dump(modelo_arima, 'modelo/auto_arima.joblib')

# Carregando o modelo salvo
modelo_carregado = joblib.load('modelo/auto_arima.joblib')

# Realizando a previsão para dois meses
forecast = modelo_carregado.predict(h=h, level=[90])

# Formatando o DataFrame de previsões
forecast = (
    forecast[['ds', 'AutoARIMA']]  # Selecionando colunas relevantes
    .reset_index(drop=True)  # Reiniciando o índice
    .rename(columns={'ds': 'data', 'AutoARIMA': 'preco_previsto_brent'})  # Renomeando colunas
)

# Arredondando os valores previstos para duas casas decimais
forecast['preco_previsto_brent'] = forecast['preco_previsto_brent'].apply(lambda x: round(x, 2))

forecast.head(10)

/home/spark/source/repos/fiap-dataanalysis-techchallenge-fase4/.venv/lib/python3.12/site-packages/statsforecast/core.py:494: FutureWarning:

In a future version the predictions will have the id as a column. You can set the `NIXTLA_ID_AS_COL` environment variable to adopt the new behavior and to suppress this warning.



data  preco_previsto_brent
0 2024-11-05                 74.64
1 2024-11-06                 74.34
2 2024-11-07                 74.39
3 2024-11-08                 74.55
4 2024-11-11                 74.63
5 2024-11-12                 74.60
6 2024-11-13                 74.55
7 2024-11-14                 74.57
8 2024-11-15                 74.54
9 2024-11-18                 74.49

In [230]:
forecast.to_csv('./output/sor/forecast.csv', index=False)